In [1]:
import pandas as pd
from math import radians, sin, cos, sqrt, atan2

'''
    LAT LON MUNICIPIOS & FILTRO CUNDIBOY
'''
latlon = pd.read_excel('DIVIPOLA_Municipios_FIXED.xlsx')
latlon.dropna(inplace=True)
cundiboy = latlon[(latlon['DEPARTAMENTO'] == 'BOYACÁ') | (latlon['DEPARTAMENTO'] == 'CUNDINAMARCA') | (latlon["DEPARTAMENTO"] == "BOGOTÁ, D.C.")]
cundiboy['MUNICIPIO'] = cundiboy['MUNICIPIO'].str.normalize('NFKD').str.encode('ascii', errors='ignore').str.decode('utf-8')
cundiboy['MUNI'] = cundiboy['MUNICIPIO'].copy()
cundiboy.set_index('MUNI', inplace=True)

'''
    PRODUCCION MUNICIPIOS
'''
DF = pd.read_csv("datos.csv", sep=";")
DF.rename(columns={'Municipio':'MUNICIPIO', 'Departamento':'DEPARTAMENTO', 'Producción':'PROD'}, inplace=True)

DF['MUNICIPIO'] = DF['MUNICIPIO'].str.normalize('NFKD').str.encode('ascii', errors='ignore').str.decode('utf-8')
DF['MUNICIPIO'] = DF['MUNICIPIO'].str.upper()
DF['MUNI'] = DF['MUNICIPIO'].copy()
DF.set_index('MUNI', inplace=True)
DF

'''
    FILTRO POR PERCENTIL DE PRODUCCION
'''
cundiboy = cundiboy.join(DF,lsuffix='cundi', how='inner')
cundiboy = cundiboy[['LATITUD', 'LONGITUD', 'PROD', 'MUNICIPIO']]
percentile = cundiboy['PROD'].quantile(.95)
cundiboy = cundiboy[ cundiboy['PROD']>percentile]
cundiboy

C:\Users\ari_r\AppData\Local\Temp\ipykernel_12348\2395960640.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  cundiboy['MUNICIPIO'] = cundiboy['MUNICIPIO'].str.normalize('NFKD').str.encode('ascii', errors='ignore').str.decode('utf-8')
C:\Users\ari_r\AppData\Local\Temp\ipykernel_12348\2395960640.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  cundiboy['MUNI'] = cundiboy['MUNICIPIO'].copy()


LATITUD   LONGITUD       PROD         MUNICIPIO
MUNI                                                              
CAPARRAPI         5.381501 -74.521236  467596.41         CAPARRAPI
CHITARAQUE        5.984395 -73.425824  291383.95        CHITARAQUE
GRANADA           4.523485 -74.337246  193945.42           GRANADA
LA PENA           5.204599 -74.407866  187565.11           LA PENA
LA VICTORIA       5.507008 -74.241627  179364.07       LA VICTORIA
MONIQUIRA         5.863370 -73.558525  182703.96         MONIQUIRA
QUEBRADANEGRA     5.099981 -74.494511  151381.82     QUEBRADANEGRA
SAN JOSE DE PARE  5.994154 -73.543865  452881.09  SAN JOSE DE PARE
SANTANA           6.057615 -73.489748  240865.54           SANTANA
SIACHOQUE         5.498748 -73.216818  176681.82         SIACHOQUE
TAUSA             5.170527 -73.958196  296517.90             TAUSA
TOGUI             5.921830 -73.489218  203098.00             TOGUI
VILLAPINZON       5.227299 -73.577259  314474.43       VILLAPINZON

In [2]:
import folium
import requests
import json

# Define the OSRM server URL
osrm_url = "http://router.project-osrm.org/route/v1/driving/"

# Initialize the map centered on the average coordinates
center_lat = cundiboy['LATITUD'].mean()
center_lon = cundiboy['LONGITUD'].mean()
m = folium.Map(location=[center_lat, center_lon], zoom_start=9)

# Function to calculate the route using OSRM
def calculate_route(source, destination):
    url = osrm_url + f"{source[1]},{source[0]};{destination[1]},{destination[0]}?overview=full&geometries=geojson"
    response = requests.get(url)
    data = json.loads(response.text)
    route = data['routes'][0]['geometry']['coordinates']
    distance = data['routes'][0]['distance']
    return route, distance

def fix(r):
  r2 = []
  for e in r:
    r2.append([e[1],e[0]])
  return r2

rutas, dist = {},{}
# Loop through pairs of municipalities to find direct trips and draw routes on the map
for i in range(len(cundiboy)):
    lai = cundiboy.index[i]
    for j in range(i+1, len(cundiboy)):
        laj = cundiboy.index[j]
        source = (cundiboy.loc[lai, 'LATITUD'], cundiboy.loc[lai, 'LONGITUD'])
        destination = (cundiboy.loc[laj, 'LATITUD'], cundiboy.loc[laj, 'LONGITUD'])
        route, distance = calculate_route(source, destination)
        rutas[lai,laj] = route
        dist[lai,laj] = distance
        folium.PolyLine(fix(route), color='red', weight=4).add_to(m)

# Add markers for each municipality
for index, row in cundiboy.iterrows():
    folium.Marker([row['LATITUD'], row['LONGITUD']], tooltip=row['MUNICIPIO']).add_to(m)

# Display the map